<div align="center"> 

**hopa1029, klfl1012**

<img src="s_purple.png" alt="drawing" width="2000" height= 200/>




# Übungsblatt 2 - Dispostion
__________________________________________________________________________________________________________________________________________________________________________________________________________________

**DSCB310 – Datenanalyse und Business Intelligence 1**  

Wintersemester 22/23

##### Gliederung des Notebooks:

1. Ziel der Datenanalyse für die Disposition
   
2. Fragestellungen:

   - D1: Prüfen Sie, ob es beim Produkt 13176 auffällige Muster beim Wiederbestellverhalten gibt.
  
   - D2: Spielen die Artikel aus dem Department „produce“ in allen Counties eine gleich große Rolle?
  
   - D3: Welche Counties sind sich ähnlich in Hinblick auf die jeweiligen „Top 10“-Produkte?
  
3. Zusätzliche Fragestellungen

##### Import und Datensatz: 

**Imports:**

in d1  und schauen obs als ersatzprodukt verwendet wurde mit classifier featuere importance



In [2]:
import numpy as np
import matplotlib.pyplot as plt
import pandas as pd
import os 
import random
import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go
from scipy.stats import chi2_contingency

**Datensatz:**

-- erklärung der einzelnen attribute --

In [3]:
df = pd.read_parquet("DSCB310 - UE2 - Shopping Carts.parquet")

In [4]:
df.reset_index(inplace=True)
df.groupby("order_id").agg(order_size=("add_to_cart_order","max")).reset_index()
df = pd.merge(df,df.groupby("order_id").agg(order_size=("add_to_cart_order","max")).reset_index())

wir fügen noch ein weiteres Attribut welche die order_size beschreibt hinzu

In [5]:
df.head()

index  order_id  product_id  add_to_cart_order  reordered  user_id  \
0  5006171         1       13176                  6          0   112108   
1  5006176         1       11109                  2          1   112108   
2  5006175         1       10246                  3          0   112108   
3  5006174         1       22035                  8          1   112108   
4  5006173         1       49683                  4          0   112108   

   order_number  order_dow  order_hour_of_day  days_since_prior_order  tip  \
0             4          4                 10                     9.0    1   
1             4          4                 10                     9.0    1   
2             4          4                 10                     9.0    1   
3             4          4                 10                     9.0    1   
4             4          4                 10                     9.0    1   

                                    product_name  aisle_id  department_id  \
0                         Bag of Organic Bananas        24              4   
1  Organic 4% Milk Fat Whole Milk Cottage Cheese       108             16   
2                          Organic Celery Hearts        83              4   
3                    Organic Whole String Cheese        21             16   
4                                 Cucumber Kirby        83              4   

   department                 aisle county  order_size  
0     produce          fresh fruits   Inyo           8  
1  dairy eggs  other creams cheeses   Inyo           8  
2     produce      fresh vegetables   Inyo           8  
3  dairy eggs       packaged cheese   Inyo           8  
4     produce      fresh vegetables   Inyo           8

##  Ziel der Datenanalyse für die Disposition:

#### Aufgabestellung

Erkenntnisse über die regionalen Unterschiede im 
Kaufverhalten der Kunden. Im Fokus sollten dabei die räumlichen Unterschiede des Absatzes bspw. in 
Bezug  auf  die  Produktkategorien,  die  „Gänge“ oder umsatzstarke Produkte stehen.  Die  Disposition 
erhofft sich dadurch eine bessere Versorgung der einzelnen Counties.

Die Disponenten, die für die 
Belieferung  der  Zentren  verantwortlich  sind,  wünschen  sich  Informationen  darüber,  welche  Produkte 
(bzw. Kategorien oder „Gänge“) in welchem County stärker, schwächer oder eher durchschnittlich 
nachgefragt  werden.  Auf  dieser  Basis  soll  die  Belieferung  der  Distributionszentren  optimiert  werden.

Uns sind alle counties in californien gegeben außer butte

### 1. Grundlegende Erkenntnisse

Die stärksten und schwächsten Regionen

In [104]:
df_regional = df.groupby("county").agg(orders = ("order_id","nunique")).reset_index()
df_regional = df_regional.sort_values("orders",ascending=False)

In [6]:
fig = go.Figure()

for county in df_regional.county.unique():

    if df_regional.loc[df_regional.county == county].orders.values >= df_regional.orders.mean():
        color= px.colors.sequential.Purpor[5]
    
        fig.add_trace (go.Bar(
            x= df_regional.loc[df_regional.county == county].county,
            y= df_regional.loc[df_regional.county == county].orders,
            showlegend= False,
            marker= dict(color= color),
            width= 0.8,
            name= f"{df_regional.loc[df_regional.county == county].county}",
            hovertemplate = f"<b>{df_regional.loc[df_regional.county == county].county.values[0]}</b><br><br>" +
                "Bestellungen: %{y}<br>" +
                "<extra></extra>"
        ))

    else:
        color= px.colors.sequential.Greys[3]

        fig.add_trace (go.Bar(
            x= df_regional.loc[df_regional.county == county].county,
            y= df_regional.loc[df_regional.county == county].orders,
            showlegend= False,
            marker= dict(color= color),
            width= 0.8,
            name= f"{df_regional.loc[df_regional.county == county].county}",
            hovertemplate = f"<b>{df_regional.loc[df_regional.county == county].county.values[0]}</b><br><br>" +
                "Bestellungen: %{y}<br>" +
                "<extra></extra>"
        ))


fig.add_annotation(
    x=55,
    y=df_regional[df_regional.county == "Placer"]["orders"].values[0],
    text="Problemfälle",
    font_color= px.colors.sequential.Greys[5],
    arrowcolor= px.colors.sequential.Greys[5]
)

fig.add_hline(
    y= df_regional.orders.mean(),
    line_dash= "dot",
    line_color= px.colors.sequential.Greys[5],
    opacity= 1
)

fig.add_annotation(
    x= 50,
    y= df_regional.orders.mean(),
    text=f"Median: {df_regional.orders.median().round(2)}",
    font_color= px.colors.sequential.Greys[5],
    arrowcolor= px.colors.sequential.Greys[5]
)

fig.update_layout(title= dict(text= "<b>Bestellungen pro County</b>", font_size= 20, xanchor= "center", yanchor= "top", y=0.935, x=0.475), legend_title_text = "<b>Counties</b>", height= 500)
fig.update_xaxes(title_text="<b>Counties</b>", ticks= "outside")
fig.update_yaxes(title_text="<b>Anzahl an Bestellungen</b>", ticks= "outside", showgrid= True, gridcolor= "grey")
fig.update_layout(plot_bgcolor= "white", xaxis= dict(linecolor= "black"), yaxis= dict(linecolor= "black"))
fig.show()

Die Counties Placer und San Bernandino besitzen so wenig Bestellungen, dass großflächige Analysen bei diesen counties wenig Sinn ergibt und es mehr Sinn macht sich die Bestellungen in diesen counties einzeln anzuschauen

Stärksten Produkte

In [7]:
df_product_name = df.groupby("product_name").agg(coun = ("product_name","count")).reset_index().sort_values("coun",ascending=False)

In [8]:
fig = go.Figure()
for i in df_product_name.head(10).coun:
    df_an = df_product_name.head(10)[df_product_name.head(10).coun == i]

    if df_an.head().coun.values[0] > df_product_name.head(10).coun.median():
        color = px.colors.sequential.Purpor[5]

        fig.add_trace (go.Bar(
            x= df_an.product_name,
            y= df_an.coun,
            showlegend= True,
            marker= dict(color= color),
            width= 0.8,
            base= 0,
            legendgroup= f"{df_an.product_name.values}",
            name= f"{df_an.product_name.values[0]}",
            hovertemplate = f"<b>{df_an.product_name.values[0]}</b><br><br>" +
                "Bestellungen: %{y}<br>" +
                "<extra></extra>"
        ))
        
    else:
        color= px.colors.sequential.Greys[3]

        fig.add_trace (go.Bar(
            x= df_an.product_name,
            y= df_an.coun,
            showlegend= True,
            marker= dict(color= color),
            width= 0.8,
            base= 0,
            legendgroup= f"{df_an.product_name.values}",
            name= f"{df_an.product_name.values[0]}",
            hovertemplate = f"<b>{df_an.product_name.values[0]}</b><br><br>" +
                "Bestellungen: %{y}<br>" +
                "<extra></extra>"
        ))

fig.add_hline(
 y= df_product_name.head(10).coun.median(),
 opacity= 1,
 line_dash= "dot",
 line_color= px.colors.sequential.Greys[5],
 
)
fig.add_annotation(
    x=9,
    y=df_product_name.head(10).coun.median(),
    text=f"Median: {df_product_name.head(10).coun.median().round(2)}",
    font_color= px.colors.sequential.Greys[5],
    arrowcolor= px.colors.sequential.Greys[5],

)
fig.update_layout(title= dict(text= "<b>Top 10 Produkte nach Verkaufszahlen</b>", font_size= 20, xanchor= "center", yanchor= "top", y=0.935, x=0.475), legend_title_text = "<b>Produkte</b>", height= 500)
#fig.update_xaxes(title_text="<b>Produtke</b>", ticks= "outside")
fig.update_yaxes(title_text="<b>Anzahl an Bestellungen</b>", ticks= "outside", showgrid= True, gridcolor= "grey")
fig.update_layout(plot_bgcolor= "white", xaxis= dict(linecolor= "black"), yaxis= dict(linecolor= "black"))
fig.show()

Stärksten department

In [9]:
df_aisle = df.groupby("aisle").agg(coun = ("aisle","count")).reset_index().sort_values("coun",ascending=False)

In [10]:
fig = go.Figure()
for i in df_aisle.head(10).coun:
    df_an = df_aisle.head(10)[df_aisle.head(10).coun == i]

    if df_an.head().coun.values[0] > df_aisle.head(10).coun.median():
        color = px.colors.sequential.Purpor[5]

        fig.add_trace (go.Bar(
            x= df_an.aisle,
            y= df_an.coun,
            showlegend= True,
            marker= dict(color= color),
            width= 0.8,
            base= 0,
            legendgroup= f"{df_an.aisle.values}",
            name= f"{df_an.aisle.values[0]}",
            hovertemplate = f"<b>{df_an.aisle.values[0]}</b><br><br>" +
                "Bestellungen: %{y}<br>" +
                "<extra></extra>"
        ))
        
    else:
        color= px.colors.sequential.Greys[3]

        fig.add_trace (go.Bar(
            x= df_an.aisle,
            y= df_an.coun,
            showlegend= True,
            marker= dict(color= color),
            width= 0.8,
            base= 0,
            legendgroup= f"{df_an.aisle.values}",
            name= f"{df_an.aisle.values[0]}",
            hovertemplate = f"<b>{df_an.aisle.values[0]}</b><br><br>" +
                "Bestellungen: %{y}<br>" +
                "<extra></extra>"
        ))

fig.add_hline(
 y= df_aisle.head(10).coun.median(),
 opacity= 1,
 line_dash= "dot",
 line_color= px.colors.sequential.Greys[5],
 
)
fig.add_annotation(
    x=9,
    y=df_aisle.head(10).coun.median(),
    text=f"Median: {df_aisle.head(10).coun.median().round(2)}",
    font_color= px.colors.sequential.Greys[5],
    arrowcolor= px.colors.sequential.Greys[5],

)
fig.update_layout(title= dict(text= "<b>Top 10 Gänge nach Verkaufszahlen</b>", font_size= 20, xanchor= "center", yanchor= "top", y=0.935, x=0.475), legend_title_text = "<b>Gänge</b>", height= 500)
#fig.update_xaxes(title_text="<b>Produtke</b>", ticks= "outside")
fig.update_yaxes(title_text="<b>Anzahl an Bestellungen</b>", ticks= "outside", showgrid= True, gridcolor= "grey")
fig.update_layout(plot_bgcolor= "white", xaxis= dict(linecolor= "black"), yaxis= dict(linecolor= "black"))
fig.show()

Stärksten department

In [11]:
df_department = df.groupby("department").agg(coun = ("department","count")).reset_index().sort_values("coun",ascending=False)

In [12]:
fig = go.Figure()
for i in df_department.head(10).coun:
    df_an = df_department.head(10)[df_department.head(10).coun == i]

    if df_an.head().coun.values[0] > df_department.head(10).coun.median():
        color = px.colors.sequential.Purpor[5]

        fig.add_trace (go.Bar(
            x= df_an.department,
            y= df_an.coun,
            showlegend= True,
            marker= dict(color= color),
            width= 0.8,
            base= 0,
            legendgroup= f"{df_an.department.values}",
            name= f"{df_an.department.values[0]}",
            hovertemplate = f"<b>{df_an.department.values[0]}</b><br><br>" +
                "Bestellungen: %{y}<br>" +
                "<extra></extra>"
        ))
        
    else:
        color= px.colors.sequential.Greys[3]

        fig.add_trace (go.Bar(
            x= df_an.department,
            y= df_an.coun,
            showlegend= True,
            marker= dict(color= color),
            width= 0.8,
            base= 0,
            legendgroup= f"{df_an.department.values}",
            name= f"{df_an.department.values[0]}",
            hovertemplate = f"<b>{df_an.department.values[0]}</b><br><br>" +
                "Bestellungen: %{y}<br>" +
                "<extra></extra>"
        ))

fig.add_hline(
 y= df_department.head(10).coun.median(),
 opacity= 1,
 line_dash= "dot",
 line_color= px.colors.sequential.Greys[5],
 
)
fig.add_annotation(
    x=9,
    y=df_department.head(10).coun.median(),
    text=f"Median: {df_department.head(10).coun.median().round(2)}",
    font_color= px.colors.sequential.Greys[5],
    arrowcolor= px.colors.sequential.Greys[5],

)
fig.update_layout(title= dict(text= "<b>Top 10 Kategorien nach Verkaufszahlen</b>", font_size= 20, xanchor= "center", yanchor= "top", y=0.935, x=0.475), legend_title_text = "<b>Kategorien</b>", height= 500)
#fig.update_xaxes(title_text="<b>Produtke</b>", ticks= "outside")
fig.update_yaxes(title_text="<b>Anzahl an Bestellungen</b>", ticks= "outside", showgrid= True, gridcolor= "grey")
fig.update_layout(plot_bgcolor= "white", xaxis= dict(linecolor= "black"), yaxis= dict(linecolor= "black"))
fig.show()

Ordersize pro county

In [105]:
df_order_size = df.groupby(["order_id","county"])[["order_size"]].max().reset_index()
df_order_size = df_order_size.groupby("county")[["order_size"]].median().reset_index()

In [106]:
df_order_size = pd.merge(df_order_size,df_regional)

In [47]:
fig = make_subplots(specs=[[{"secondary_y": True}]])

fig.add_trace (go.Bar(
               
            x= df_order_size.county,
            y= df_order_size.order_size,
            showlegend= True,
            marker= dict(color= px.colors.sequential.Purpor[5]),
            width= 0.8,
            name="order_size",
            legendgroup= f"{df_order_size.county.values}"
        ),
        secondary_y=False)
    
fig.add_trace (go.Scatter(
               
            x= df_order_size.county,
            y= df_order_size.orders,
            mode="lines",
            showlegend= True,
            line= dict(color= px.colors.sequential.Greys[5],width=4),            
            name="Bestellungen",
            
        ),
        secondary_y=True)




fig.update_layout(title= dict(text= "<b>Bestellungen/Ordersize pro county</b>", font_size= 20, xanchor= "center", yanchor= "top", y=0.935, x=0.475), legend_title_text = "<b>Counties</b>", height= 500,
    # barmode='group',
    # bargap=0.15, # gap between bars of adjacent location coordinates.
    # bargroupgap=0.1 # gap between bars of the same location coordinate.

)

fig.show()

In [108]:
df_order_size.corr()

order_size    orders
order_size    1.000000  0.316174
orders        0.316174  1.000000

Korrelation zwischen durchschnittliche Bestellgröße mit den gesamten Bestellungen in einem County

### 2. Fragestellungen:

##### **D1:** Prüfen Sie, ob es beim Produkt 13176 auffällige Muster beim Wiederbestellverhalten gibt.

In [6]:
df_auf1 = df[df.product_id == 13176]
liste = df_auf1.groupby("user_id").agg(order_id=("order_number","min")).reset_index().order_id.to_list()
df_auf1.loc[df_auf1.order_id.isin(liste),"reordered"] = 0

In [7]:
df_auf1[df_auf1.reordered == 1]

index  order_id  product_id  add_to_cart_order  reordered  user_id  \
846      2437912        84       13176                  2          1   146875   
876      1792441        87       13176                  2          1    86142   
1018     2736512       101       13176                  3          1   153133   
1160     1177783       110       13176                  3          1    33769   
1237     4561110       118       13176                 20          1   170906   
...          ...       ...         ...                ...        ...      ...   
6132036  3941644    606853       13176                  4          1   112206   
6132178   800409    606867       13176                  6          1    31632   
6132363  3629290    606885       13176                  1          1    32829   
6132372  4211553    606886       13176                  4          1    19992   
6132455  3961519    606894       13176                  6          1    38426   

         order_number  order_dow  order_hour_of_day  days_since_prior_order  \
846                11          2                 16                     6.0   
876                40          2                 12                    16.0   
1018               13          3                 20                    30.0   
1160                4          5                 18                    20.0   
1237                2          1                  7                    10.0   
...               ...        ...                ...                     ...   
6132036            19          0                  8                     5.0   
6132178             4          0                 15                     7.0   
6132363             2          6                 15                    11.0   
6132372             2          6                 18                     6.0   
6132455            14          3                 18                    21.0   

         tip            product_name  aisle_id  department_id department  \
846        0  Bag of Organic Bananas        24              4    produce   
876        0  Bag of Organic Bananas        24              4    produce   
1018       1  Bag of Organic Bananas        24              4    produce   
1160       0  Bag of Organic Bananas        24              4    produce   
1237       1  Bag of Organic Bananas        24              4    produce   
...      ...                     ...       ...            ...        ...   
6132036    1  Bag of Organic Bananas        24              4    produce   
6132178    1  Bag of Organic Bananas        24              4    produce   
6132363    1  Bag of Organic Bananas        24              4    produce   
6132372    1  Bag of Organic Bananas        24              4    produce   
6132455    0  Bag of Organic Bananas        24              4    produce   

                aisle         county  order_size  
846      fresh fruits         Merced           9  
876      fresh fruits    Los Angeles          15  
1018     fresh fruits        Ventura          29  
1160     fresh fruits  Santa Barbara           3  
1237     fresh fruits           Yuba          27  
...               ...            ...         ...  
6132036  fresh fruits       Mariposa          18  
6132178  fresh fruits         Alpine          24  
6132363  fresh fruits       Siskiyou          14  
6132372  fresh fruits          Marin           9  
6132455  fresh fruits      San Mateo          12  

[58389 rows x 18 columns]

Es wurden 58 tausend mal Bag of Organic Bananas wiederbestellt

In [34]:
df_77 = df.groupby("user_id").agg(coun= ("order_id","nunique")).reset_index()
df_77[df_77.coun == 1]

Empty DataFrame
Columns: [user_id, coun]
Index: []

Prüfen ob es User gibt die generell nur eine Bestellung bis jetzt getätigt haben, da wir diese theoretisch abziehen müssten

In [35]:
df_banana_user = df_auf1.groupby("user_id").agg(Banana_orders = ("product_name","count")).reset_index()

In [39]:
fig= go.Figure()


fig.add_trace(
    go.Bar(
        x= ["nicht wiederbestellt"],
        y= [df_banana_user[df_banana_user.Banana_orders == 1].count().values[0]],
        name= "nicht wiederbestellt",
        marker= dict(color= px.colors.sequential.Greys[3]),
        width= 0.5,
        text= str(df_banana_user[df_banana_user.Banana_orders == 1].count().values[0]),      
        hovertemplate = f"<b>Banana Orders</b><br><br>" +
                "User: %{y}<br>" +
                "<extra></extra>"
    )
)

fig.add_trace(
    go.Bar(
        x= ["wiederbestellt"],
        y= [df_banana_user[df_banana_user.Banana_orders != 1].count().values[0]],
        name= "wiederbestellt",
        marker= dict(color= px.colors.sequential.Purpor[5]),
        width= 0.5,
        text= str(df_banana_user[df_banana_user.Banana_orders != 1].count().values[0]),      
        hovertemplate = f"<b>Banana Orders</b><br><br>" +
                "User: %{y}<br>" +
                "<extra></extra>"
    )
)

    

fig.update_layout(title= dict(text= "<b>Wiederbestellverhalten der einmaligen Bananenkäufer</b>", font_size= 20, xanchor= "center", yanchor= "top", y=0.935, x=0.475), legend_title_text = "<b>Kategorien</b>", height= 500)
fig.update_xaxes(ticks= "outside")
fig.update_yaxes(title_text="<b>Anzahl an User</b>", ticks= "outside", showgrid= True, gridcolor= "grey", tickvals= [0, 2500, 5000, 7500, 10000])
fig.update_layout(plot_bgcolor= "white", xaxis= dict(linecolor= "black"), yaxis= dict(linecolor= "black"))
fig.show()

Von allen Usern die 11 tausen Usern die mindestens einmal Bananen bestellt haben, haben rund 8 tausend wieder Banannen bestellt

In [42]:
user_1 = df_auf1[df_auf1.reordered == 1].user_id.unique()
df_user_1 = df[df.user_id.isin(user_1)]
banana_order = df_auf1.order_id.unique().tolist()
df_user_1["Banana_Org"] = False
df_user_1.loc[df_user_1.order_id.isin(banana_order),"Banana_Org"] = True
df_auf11 = df[df.product_name == "Banana"]
banana_order1 =  df_auf11.order_id.unique().tolist()
df_user_1["Banana"] = False
df_user_1.loc[df_user_1.order_id.isin(banana_order1),"Banana"] = True
df_test2 = df_user_1[df_user_1.product_id == 13176][["user_id","order_number","add_to_cart_order"]]
df_user1 = df_user_1.groupby(["user_id","order_number"])[["Banana_Org","Banana","order_size","days_since_prior_order","order_dow","tip","order_hour_of_day"]].max().reset_index()
df_user1 = pd.merge(df_user1,df_test2,how="left")

C:\Users\paulh\AppData\Local\Temp\ipykernel_2088\1845880730.py:4: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

C:\Users\paulh\AppData\Local\Temp\ipykernel_2088\1845880730.py:8: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [43]:
df_user1 = pd.merge(df_user1,df_user1.groupby("user_id").agg(wahr1=("Banana_Org","sum")).reset_index(),on="user_id")
df_user1 = pd.merge(df_user1,df_user1[df_user1.Banana_Org == False].groupby("user_id").agg(falsch1=("Banana_Org","count")).reset_index(),on="user_id")
df_user1["Value_Org"] = df_user1.wahr1 / (df_user1.wahr1 + df_user1.falsch1)

In [44]:
df_user1 = pd.merge(df_user1,df_user1.groupby("user_id").agg(wahr=("Banana","sum")).reset_index(),on="user_id")
df_user1 = pd.merge(df_user1,df_user1[df_user1.Banana == False].groupby("user_id").agg(falsch=("Banana","count")).reset_index(),on="user_id")
df_user1["Value"] = df_user1.wahr / (df_user1.wahr + df_user1.falsch)

In [25]:
df_user1.groupby("order_size")[["Value_Org"]].median().reset_index()

order_size  Value_Org
0            1   0.200000
1            2   0.203390
2            3   0.210526
3            4   0.216667
4            5   0.224490
..         ...        ...
88         100   0.056338
89         108   0.056338
90         109   0.056338
91         127   0.434783
92         145   0.434783

[93 rows x 2 columns]

In [33]:
fig = go.Figure(go.Scatter(
            mode="markers",
            x= df_user1.groupby("order_size")[["Value_Org"]].median().reset_index().order_size,
            y= df_user1.groupby("order_size")[["Value_Org"]].median().reset_index().Value_Org,
            showlegend= False,
            line= dict(color= px.colors.sequential.Purpor[5],width=4),
            #marker= dict(color= px.colors.sequential.Purpor[5]),
            #width= 0.8,
            # legendgroup= f"{df_an.product_name.values}",
            name= f"Bestellungen in denen Bananen wiederbestellt wurden",
            # hovertemplate = f"<b>{df_an.product_name.values[0]}</b><br><br>" +
            #     "Bestellungen: %{y}<br>" +
            #     "<extra></extra>"   
))
fig.update_layout(title= dict(text= "<b>Anteil an Bestellungen mit Bananen in der Bestellung bei bestimmter Bestellgröße</b>", font_size= 20, xanchor= "center", yanchor= "top", y=0.935, x=0.475), legend_title_text = "<b>Kategorien</b>",
 height= 500,
 )

fig.update_xaxes(title_text="<b>Bestellgröße</b>", ticks= "outside")
fig.update_yaxes(title_text="<b>Anteil an den Bestellungen</b>", ticks= "outside", showgrid= True, gridcolor= "grey")
fig.update_layout(plot_bgcolor= "white", xaxis= dict(linecolor= "black"), yaxis= dict(linecolor= "black"))
fig.show()




In [10]:
df_user1

user_id  order_number  Banana_Org  Banana  order_size  \
0            40             1        True   False          12   
1            40             2        True   False          13   
2            40             3       False    True          15   
3            40             4       False   False          11   
4            40             5        True   False          11   
...         ...           ...         ...     ...         ...   
208041   206168             8       False   False           4   
208042   206168             9       False   False          11   
208043   206168            10        True   False          11   
208044   206168            11       False   False          11   
208045   206168            12       False   False          13   

        days_since_prior_order  order_dow  tip  order_hour_of_day  \
0                          NaN          0    1                  9   
1                          8.0          1    0                 10   
2                         12.0          6    0                 11   
3                          8.0          0    1                 12   
4                         20.0          6    0                  9   
...                        ...        ...  ...                ...   
208041                     5.0          4    0                 16   
208042                     4.0          1    0                 17   
208043                     6.0          0    0                 18   
208044                     4.0          4    0                 21   
208045                     4.0          1    0                 14   

        add_to_cart_order  
0                     1.0  
1                     2.0  
2                     NaN  
3                     NaN  
4                     4.0  
...                   ...  
208041                NaN  
208042                NaN  
208043                7.0  
208044                NaN  
208045                NaN  

[208046 rows x 10 columns]

In [28]:
df_banana_reordered = pd.concat([df_user1,df_user1[df_user1.Banana == True].groupby('user_id').head(1).reset_index(drop=True)]).drop_duplicates(keep=False)

In [29]:
finale = df_banana_reordered.groupby(["order_dow","Banana"]).agg(count = ("order_dow","count")).reset_index()
finale["Anteil"] = 0
finale.loc[finale.Banana == True,"Anteil"] = finale.loc[finale.Banana == True]["count"]/finale.loc[finale.Banana == True]["count"].sum()
finale.loc[finale.Banana == False,"Anteil"] = finale.loc[finale.Banana == False]["count"]/finale.loc[finale.Banana == False]["count"].sum()

In [30]:
fig = go.Figure()
fig.add_trace(go.Scatter(
            x= finale.loc[finale.Banana == True].order_dow,
            y= finale.loc[finale.Banana == True].Anteil,
            showlegend= True,
            line= dict(color= px.colors.sequential.Purpor[5],width=4),
            #marker= dict(color= px.colors.sequential.Purpor[5]),
            #width= 0.8,
            # legendgroup= f"{df_an.product_name.values}",
            name= f"Bestellungen in denen Bananen wiederbestellt wurden",
            # hovertemplate = f"<b>{df_an.product_name.values[0]}</b><br><br>" +
            #     "Bestellungen: %{y}<br>" +
            #     "<extra></extra>"   
))
fig.add_trace(go.Scatter(
            x= finale.loc[finale.Banana == False].order_dow,
            y= finale.loc[finale.Banana == False].Anteil,
            showlegend= True,
            #marker= dict(color= px.colors.sequential.Greys[3]),
           # width= 0.8,
            line= dict(color= px.colors.sequential.Greys[3],width=4),  
            # legendgroup= f"{df_an.product_name.values}",
            name= f"Bestellungen ohne Bananen",
            # hovertemplate = f"<b>{df_an.product_name.values[0]}</b><br><br>" +
            #     "Bestellungen: %{y}<br>" +
            #     "<extra></extra>"   
))
fig.update_layout(title= dict(text= "<b>An welchen Tagen in der Woche wurden am meisten Bananen wiederbestellt</b>", font_size= 20, xanchor= "center", yanchor= "top", y=0.935, x=0.475), legend_title_text = "<b>Kategorien</b>",
 height= 500,
 )

fig.update_xaxes(title_text="<b>Wochentage</b>", ticks= "outside")
fig.update_yaxes(title_text="<b>Anteil an der Woche</b>", ticks= "outside", showgrid= True, gridcolor= "grey")
fig.update_layout(plot_bgcolor= "white", xaxis= dict(linecolor= "black"), yaxis= dict(linecolor= "black"))
fig.show()

In [ ]:
finale2 = df_banana_reordered.groupby(["order_hour_of_day","Banana"]).agg(count = ("order_hour_of_day","count")).reset_index()
finale2["Anteil"] = 0
finale2.loc[finale2.Banana == True,"Anteil"] = finale2.loc[finale2.Banana == True]["count"]/finale2.loc[finale2.Banana == True]["count"].sum()
finale2.loc[finale2.Banana == False,"Anteil"] = finale2.loc[finale2.Banana == False]["count"]/finale2.loc[finale2.Banana == False]["count"].sum()

In [ ]:
fig = go.Figure()
fig.add_trace(go.Scatter(
            x= finale2.loc[finale2.Banana == True].order_hour_of_day,
            y= finale2.loc[finale2.Banana == True].Anteil,
            showlegend= True,
            line= dict(color= px.colors.sequential.Purpor[5],width=4),
            #marker= dict(color= px.colors.sequential.Purpor[5]),
            #width= 0.8,
            # legendgroup= f"{df_an.product_name.values}",
            name= f"Bestellungen in denen Bananen wiederbestellt wurden",
            # hovertemplate = f"<b>{df_an.product_name.values[0]}</b><br><br>" +
            #     "Bestellungen: %{y}<br>" +
            #     "<extra></extra>"   
))
fig.add_trace(go.Scatter(
            x= finale2.loc[finale2.Banana == False].order_hour_of_day,
            y= finale2.loc[finale2.Banana == False].Anteil,
            showlegend= True,
            #marker= dict(color= px.colors.sequential.Greys[3]),
           # width= 0.8,
            line= dict(color= px.colors.sequential.Greys[3],width=4),  
            # legendgroup= f"{df_an.product_name.values}",
            name= f"Bestellungen ohne Bananen",
            visible= False
            # hovertemplate = f"<b>{df_an.product_name.values[0]}</b><br><br>" +
            #     "Bestellungen: %{y}<br>" +
            #     "<extra></extra>"   
))
fig.update_layout(title= dict(text= "<b>An welchen Tagen in der Woche wurden am meisten Bananen wiederbestellt</b>", font_size= 20, xanchor= "center", yanchor= "top", y=0.935, x=0.475), legend_title_text = "<b>Kategorien</b>",
 height= 500,
 )

fig.update_xaxes(title_text="<b>Wochentage</b>", ticks= "outside")
fig.update_yaxes(title_text="<b>Anteil an der Woche</b>", ticks= "outside", showgrid= True, gridcolor= "grey")
fig.update_layout(plot_bgcolor= "white", xaxis= dict(linecolor= "black"), yaxis= dict(linecolor= "black"))
fig.show()

In [ ]:
df_lala = df_auf1.groupby("county").agg(summe=("reordered","sum"),coun = ("reordered","count")).reset_index()

In [ ]:
fig = go.Figure(go.Scatter(
    x=df_auf1.groupby("county").agg(summe=("reordered","sum"),coun = ("reordered","count")).reset_index().county,
    y=df_auf1.groupby("county").agg(summe=("reordered","sum"),coun = ("reordered","count")).reset_index().summe / df_auf1.groupby("county").agg(summe=("reordered","sum"),coun = ("reordered","count")).reset_index().coun,
    line= dict(color= px.colors.sequential.Purpor[5],width=4),

))
fig.update_layout(title= dict(text= "<b>Anteil der Wiederbestellung an Bananen an Gesamtbananenbestellungen</b>", font_size= 20, xanchor= "center", yanchor= "top", y=0.935, x=0.475), legend_title_text = "<b>Kategorien</b>",
 height= 500,
 )

fig.update_xaxes(title_text="<b>Counties</b>", ticks= "outside")
fig.update_yaxes(title_text="<b>Anteil der Wiederbestellungen</b>", ticks= "outside", showgrid= True, gridcolor= "grey")
fig.update_layout(plot_bgcolor= "white", xaxis= dict(linecolor= "black"), yaxis= dict(linecolor= "black"))
fig.show()

In [ ]:
df_user1["Summe"] = df_user1.groupby("user_id")[["days_since_prior_order"]].cumsum()
df_banana = df_user1[df_user1.Banana == True]
df_banana["Days"] = df_banana.Summe - df_banana.Summe.shift()

C:\Users\paulh\AppData\Local\Temp\ipykernel_19280\204625665.py:3: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [ ]:
df_banana.loc[df_banana.groupby("user_id")["order_number"].idxmin(),"Days"] = None
df_banana.loc[(df_banana.Days.isna())&(df_banana.Days.shift().isna()),"Days"] = df_banana.loc[(df_banana.Days.isna())&(df_banana.Days.shift().isna())].Summe

In [ ]:
df_banana["user_next"] = df_banana.user_id.shift()

C:\Users\paulh\AppData\Local\Temp\ipykernel_19280\3445802266.py:1: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy



In [ ]:
fig = go.Figure(go.Scatter(
    mode="markers",
    x=df_banana.groupby("Days").agg(coun=("Days","count")).reset_index().Days,
    y=df_banana.groupby("Days").agg(coun=("Days","count")).reset_index().coun,
    line= dict(color= px.colors.sequential.Purpor[5],width=7)

))
fig.update_layout(title= dict(text= "<b>Anteil der Wiederbestellung an Bananen an Gesamtbananenbestellungen</b>", font_size= 20, xanchor= "center", yanchor= "top", y=0.935, x=0.475), legend_title_text = "<b>Kategorien</b>",
 height= 500,
 )

fig.update_xaxes(title_text="<b>Wieviel Tage sind seit letzer Bananenbestellung vergangen</b>", ticks= "outside")
fig.update_yaxes(title_text="<b>Anzahl</b>", ticks= "outside", showgrid= True, gridcolor= "grey",type="log")
fig.update_layout(plot_bgcolor= "white", xaxis= dict(linecolor= "black"), yaxis= dict(linecolor= "black"))
fig.show()

In [31]:
df_user1["Orders"] = 1
df_user1["Cum"] = df_user1.Orders.cumsum()
df_user1["Banana_next"] = df_user1.Banana.shift()
df_user1[df_user1.Banana == False].groupby("user_id")["Orders"].cumsum()

2          1
3          2
9          1
10         2
11         3
          ..
208039     6
208041     7
208042     8
208044     9
208045    10
Name: Orders, Length: 141199, dtype: int64

In [33]:
df_user1["user_next"] = df_user1.user_id.shift()
df_user1.loc[df_user1.Banana == False,"Orders"] = df_user1[df_user1.Banana == False].groupby("user_id")["Orders"].cumsum()
df_user1.loc[df_user1.user_id != df_user1.user_next,"Orders"] = 0

In [36]:
df_user1.groupby("Orders").agg(count = ("Orders","count"))

count
Orders       
0        8450
1       66548
3        7688
6        7113
10       6594
...       ...
4465       38
4560       30
4656       25
4753       14
4851        8

[99 rows x 1 columns]

In [41]:
fig = go.Figure(go.Scatter(
    mode="markers",
    x=df_user1.groupby("Orders").agg(coun = ("Orders","count")).reset_index().Orders,
    y=df_user1.groupby("Orders").agg(coun = ("Orders","count")).reset_index().coun,
    line= dict(color= px.colors.sequential.Purpor[5],width=7)

))
fig.update_layout(title= dict(text= "<b>Wie viel Bestellungen die Letzte Bananenbestellung her ist</b>", font_size= 20, xanchor= "center", yanchor= "top", y=0.935, x=0.475), legend_title_text = "<b>Kategorien</b>",
 height= 500,
 )

fig.update_xaxes(title_text="<b>Wieviel Bestellungen sind seit letzer Bananenbestellung vergangen</b>", ticks= "outside")
fig.update_yaxes(title_text="<b>Anzahl</b>", ticks= "outside", showgrid= True, gridcolor= "grey",type="log")
fig.update_layout(plot_bgcolor= "white", xaxis= dict(linecolor= "black"), yaxis= dict(linecolor= "black"))
fig.show()

In [55]:
df_user1.loc[(df_user1.Value + df_user1.Value_Org > 0.75)&(df_user1.Value != 0)].user_id.unique()

array([    40,    118,    906,   1850,   2413,   2488,   2522,   2610,
         3391,   4101,   4570,   5220,   5353,   5805,   6378,   6610,
         7139,   7971,   8061,   8930,   9819,  10093,  10604,  10613,
        10924,  11687,  12538,  14880,  15133,  16125,  16181,  17660,
        18176,  18831,  18964,  20452,  20460,  20596,  20630,  21001,
        21003,  21232,  21346,  21752,  22063,  22784,  23323,  23371,
        23726,  24505,  24651,  24938,  25791,  27254,  27354,  27429,
        27782,  28113,  28556,  28947,  29313,  30910,  31508,  31617,
        31650,  32303,  32451,  33908,  34121,  34466,  35189,  35227,
        35348,  36004,  36208,  37226,  37522,  37528,  38426,  39634,
        39934,  40018,  41356,  41480,  41674,  42300,  42776,  43794,
        44087,  44283,  44332,  44767,  44785,  45341,  45935,  45958,
        46039,  46753,  47310,  47661,  48763,  48976,  49445,  49566,
        51020,  51485,  53693,  54306,  54693,  56406,  56817,  56985,
      

In [58]:
df_user2 = df_user1.groupby("user_id")[["wahr1","falsch1","Value_Org","wahr","falsch","Value"]].max().reset_index()

In [66]:
df_user2.loc[df_user2.user_id.isin(df_user1.loc[(df_user1.Value + df_user1.Value_Org > 0.8)].user_id.unique())]

user_id  wahr1  falsch1  Value_Org  wahr  falsch     Value
0          40      7        2   0.777778     1       8  0.111111
4         118     22        6   0.785714     1      27  0.035714
11        200      8        1   0.888889     0       9  0.000000
26        768     31        3   0.911765     0      34  0.000000
27        847     35        3   0.921053     0      38  0.000000
...       ...    ...      ...        ...   ...     ...       ...
8079   204617      5        1   0.833333     0       6  0.000000
8092   204842     28        3   0.903226     0      31  0.000000
8128   205600     14        2   0.875000     0      16  0.000000
8139   205985      9        1   0.900000     0      10  0.000000
8143   206061     13        1   0.928571     0      14  0.000000

[663 rows x 7 columns]

In [68]:
df_user2.loc[df_user2.Value_Org < 0.25]

user_id  wahr1  falsch1  Value_Org  wahr  falsch     Value
1          42      2       15   0.117647     0      17  0.000000
5         140     14       63   0.181818     1      76  0.012987
7         168      3       19   0.136364     0      22  0.000000
9         195      3       56   0.050847     0      59  0.000000
12        236      2       43   0.044444     3      42  0.066667
...       ...    ...      ...        ...   ...     ...       ...
8140   205993      4       42   0.086957     0      46  0.000000
8141   206030      3       35   0.078947    13      25  0.342105
8144   206073      3       10   0.230769     0      13  0.000000
8149   206162      2       17   0.105263     0      19  0.000000
8150   206168      2       10   0.166667     0      12  0.000000

[2842 rows x 7 columns]

In [88]:
df_user2.loc[(df_user2.Value_Org > 0.75)&(df_user2.Value == 0)]

user_id  wahr1  falsch1  Value_Org  wahr  falsch     Value
0          40      7        2   0.777778     1       8  0.111111
4         118     22        6   0.785714     1      27  0.035714
11        200      8        1   0.888889     0       9  0.000000
26        768     31        3   0.911765     0      34  0.000000
27        847     35        3   0.921053     0      38  0.000000
...       ...    ...      ...        ...   ...     ...       ...
8092   204842     28        3   0.903226     0      31  0.000000
8125   205549     12        3   0.800000     0      15  0.000000
8128   205600     14        2   0.875000     0      16  0.000000
8139   205985      9        1   0.900000     0      10  0.000000
8143   206061     13        1   0.928571     0      14  0.000000

[641 rows x 7 columns]

In [86]:
df_user2.loc[(df_user2.Value_Org > 0.25)&(df_user2.Value_Org < 0.75)&(df_user2.Value == 0)]

user_id  wahr1  falsch1  Value_Org  wahr  falsch  Value
6         141      2        2   0.500000     0       4    0.0
8         192      3        3   0.500000     0       6    0.0
10        196      2        1   0.666667     0       3    0.0
14        413     12        8   0.600000     0      20    0.0
15        416      2        2   0.500000     0       4    0.0
...       ...    ...      ...        ...   ...     ...    ...
8136   205864      3        6   0.333333     0       9    0.0
8142   206045     12       21   0.363636     0      33    0.0
8145   206116      2        4   0.333333     0       6    0.0
8147   206146      4        6   0.400000     0      10    0.0
8148   206153      5        9   0.357143     0      14    0.0

[3277 rows x 7 columns]

In [82]:
df_user2.loc[df_user2.Value_Org < 0.25].Value.median()

0.0

In [83]:
df_user2.loc[(df_user2.Value_Org > 0.25)&(df_user2.Value_Org < 0.75)].Value.median()

0.0

In [84]:
df_user2.loc[df_user2.Value_Org > 0.75].Value.median()

0.0

In [74]:
px.histogram(df_user2,x=df_user2.Value_Org,nbins=50)

In [75]:
px.histogram(df_user2,x=df_user2.Value_Org + df_user2.Value,nbins=50)

In [67]:
df_user2

user_id  wahr1  falsch1  Value_Org  wahr  falsch     Value
0          40      7        2   0.777778     1       8  0.111111
1          42      2       15   0.117647     0      17  0.000000
2          65      8        7   0.533333     1      14  0.066667
3          85      3        4   0.428571     1       6  0.142857
4         118     22        6   0.785714     1      27  0.035714
...       ...    ...      ...        ...   ...     ...       ...
8146   206132      2        4   0.333333     1       5  0.166667
8147   206146      4        6   0.400000     0      10  0.000000
8148   206153      5        9   0.357143     0      14  0.000000
8149   206162      2       17   0.105263     0      19  0.000000
8150   206168      2       10   0.166667     0      12  0.000000

[8151 rows x 7 columns]

In [63]:
(df_user1.Value + df_user1.Value_Org).mean()

0.3940746202052734

##### **D2:** Spielen die Artikel aus dem Department „produce“ in allen Counties eine gleich große Rolle?

In [ ]:
df_d2 = df.groupby(["county","department"]).agg(anzahl=("department","count")).reset_index()

In [ ]:
counties = df_d2.county.unique().tolist()
for i in counties:
    df_d2.loc[df_d2["county"] == i,"rank"] = df_d2.loc[df_d2["county"] == i].anzahl.rank(method="min",ascending=False)

Annahme: 

Gleiche Rolle bedeutet welchen Platz das department im Vergleich zu den anderen departments in dem county besitzt, basierend auf den Absatzzahlen

In [ ]:
df_2d = df_d2[df_d2.department == "produce"]
df_2d

county department  anzahl  rank
19            Alameda    produce    5072   1.0
40             Alpine    produce   33453   1.0
61             Amador    produce   41772   1.0
82          Calaveras    produce  144011   1.0
103            Colusa    produce   11451   1.0
124      Contra Costa    produce   25817   1.0
145         Del Norte    produce    4010   2.0
165         El Dorado    produce    4157   1.0
186            Fresno    produce  109085   1.0
207             Glenn    produce   97957   1.0
228          Humboldt    produce    1179   1.0
249          Imperial    produce   47752   1.0
270              Inyo    produce   16509   1.0
291              Kern    produce   96742   1.0
312             Kings    produce   10140   1.0
333              Lake    produce   44237   1.0
354            Lassen    produce    4932   1.0
375       Los Angeles    produce   44082   1.0
396            Madera    produce   36394   1.0
417             Marin    produce   18051   1.0
438          Mariposa    produce   66013   1.0
459         Mendocino    produce   16364   1.0
480            Merced    produce   42878   1.0
501             Modoc    produce   20148   1.0
521              Mono    produce    9413   1.0
542          Monterey    produce   70904   1.0
563              Napa    produce    3911   1.0
584            Nevada    produce   17533   1.0
605            Orange    produce  112803   1.0
619            Placer    produce      98   1.0
640            Plumas    produce   19718   1.0
661         Riverside    produce   12117   1.0
682        Sacramento    produce   38146   1.0
703        San Benito    produce   24929   1.0
715    San Bernardino    produce      19   3.0
736         San Diego    produce    4633   1.0
757     San Francisco    produce   48118   1.0
778       San Joaquin    produce    2415   1.0
799   San Luis Obispo    produce    8842   1.0
819         San Mateo    produce   31647   1.0
840     Santa Barbara    produce   60914   1.0
861       Santa Clara    produce   23649   1.0
882        Santa Cruz    produce   52390   1.0
903            Shasta    produce   11091   1.0
924            Sierra    produce    5133   2.0
945          Siskiyou    produce   22394   1.0
966            Solano    produce   10236   1.0
987            Sonoma    produce    5446   1.0
1008       Stanislaus    produce    8695   1.0
1029           Sutter    produce   87854   1.0
1050           Tehama    produce    1548   2.0
1067          Trinity    produce     495   1.0
1087           Tulare    produce    5380   1.0
1108         Tuolumne    produce    9217   1.0
1129          Ventura    produce   67083   1.0
1150             Yolo    produce   24880   1.0
1171             Yuba    produce   30046   1.0

wie man sieht ist das departmen produce, welches aus obst und gemüseprodukten besteht in jedem county außer 4 ausnahmen das Umsatzstärkste

Die Ausnahmen enthalten die counties Del Norte, Sierra, San Bernardino	und Tehama

San Bernardino bestitz wegen seinen niedrigen ausleihzahlen, verglichen zum rest nur wenig statistische signifikanz

In [101]:
from urllib.request import urlopen
import json
with urlopen('https://raw.githubusercontent.com/plotly/datasets/master/geojson-counties-fips.json') as response:
    geojsn = json.load(response)

In [102]:
a = geojsn["features"].__len__()
for i in range(a,0,-1):
    if geojsn["features"][i-1]["properties"]["STATE"] != "06":
        geojsn["features"].pop(i-1)
#erschaffen uns eine geojson datei mit allen counties in kalifornien

In [ ]:
colorscales_2d = [((0,"#948a9c"),(1,"#948a9c")),
                ((0,"#7514c4"),(1,"#7514c4")),
                ((0,"#330459"),(1,"#330459"))
]
exception = df_2d[df_2d["rank"]==2].county.to_list()

---Plot D2.1---

In [ ]:
fig = make_subplots(cols= 2, rows=1, specs= [[dict(type= "table"), dict(type= "choroplethmapbox")]],vertical_spacing=0.01)

fig.add_trace(
  go.Table(
    columnwidth= [2, 4, 2, 2, 2],
    header=dict(
        values=list(df_d2[df_d2.county.isin(exception)].sort_values("rank").head(6).columns)
        ),
    cells=dict(
        values=df_d2[df_d2.county.isin(exception)].sort_values("rank").head(6).T.values,
        height= 28
        )
    ),
    col= 1,
    row= 1
)




for i,b in enumerate(df_2d["rank"].unique()):
    
    fig.add_trace(go.Choroplethmapbox(geojson=geojsn, featureidkey= "properties.NAME",locations=df_2d[df_2d["rank"] == b].county,
                                    z=[i]*len(df_2d[df_2d["rank"] == b]),
                                    colorscale=colorscales_2d[i],
                                    name=b,
                                    showlegend=True,
                                    showscale=False,
                                    marker_opacity=0.6, marker_line_width=0),
                                    col=2,
                                    row=1
                                    )
fig.update_layout(mapbox_style="carto-positron",
                  mapbox_zoom=4, mapbox_center = {"lat": 36.778259, "lon": -119.417931})
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

##### **D3:** Welche Counties sind sich ähnlich in Hinblick auf die jeweiligen „Top 10“-Produkte?

In [89]:
df_d3 = df.groupby(["county","product_name"]).agg(anzahl=("product_name","count")).reset_index()
counties = df_d3.county.unique().tolist()
for i in counties:
    df_d3.loc[df_d3["county"] == i,"rank"] = df_d3.loc[df_d3["county"] == i].anzahl.rank(method="min",ascending=False)

In [90]:
df_4 = df_d3[df_d3["rank"].isin(range(11))]
df_4 = df_4.sort_values(["county","rank"])

Wir nehmen die Top 10 Produkte je county basierend auf den Absatzzahlen

In [91]:
df_13 = df_4.groupby("county").agg(coun=("county","count")).reset_index()
df_13[">10"] = df_13.coun > 10
df_4 = pd.merge(df_4,df_13)

In [92]:
fehler = df_4[df_4[">10"] == True].county.unique()
for i in fehler:
    df_4.drop(df_4[df_4.county == i].tail(df_4[df_4.county == i].coun.values[0]-10).index,inplace=True)

Da es manchmal vorkommt, dass Produkte die gleiche Anzahl an Bestellung innerhalb der Top 10 Produkte eines counties besitzen, lösen wir das Problem indem wir den Dataframe um so viel Zeilen in dem county entfernen, die es mehr als 10 sind. Wir verändern jedoch hierbei nicht den Rang eines Produkts wodurch es totzdem noch zu doppelungen des Rangs innerhalb eines countys vorkommen kann.

In [93]:
ableitung = []
test2 = []
for i in counties:
    
    for j in counties:
        score = 0
        
        for o in df_4.loc[df_4.county == i,("product_name","rank")].values:
            for z in df_4.loc[df_4.county == j,("product_name","rank")].values:
                if o[0] == z[0]:
                    score = score+1
                    if o[1] == z[1]:
                        score = score+1
        if score < 20:
        
         test2.append(i+j)
         if not(i+j in test2 and j+i in test2):
          ableitung.append([score,i,j])

Die ähnlichkeit zwischen counties prüfen wir in dem wir jeden Produkteintrag eines countys mit alledn Produkten des anderesn countys vergleichen.

Falls des Produkt enthalten ist erhöhen wir den unseren score um 1 und wenn das Produkt noch den gleichen Rang besitzt erhöhen wir den Rang ein weiteres mal um 1.

Damit ergibt sich ein Top score von 20(wenn man die gleichen counties vergleichen würde) und eine genauere Ähnlichkeit als wenn man nur auf die verschiedenen Produkte schauen würde und diese beispielsweise mit einer cosinus_similiarity abbilden würde.

In [94]:
ableitung.sort(reverse=True)

In [95]:
df_map = pd.DataFrame(ableitung,columns=["score","county1","county2"])
df_table = df_4.iloc[:, 0:4]

In [96]:
colorscales_orig = [
                px.colors.sequential.Greys[1],
                px.colors.sequential.Greys[2],
                px.colors.sequential.Greys[3],
                px.colors.sequential.Purp[3],
                px.colors.sequential.Purp[4],
                px.colors.sequential.Purp[5],
                px.colors.sequential.Purpor[4],
                px.colors.sequential.Purpor[5],
                px.colors.sequential.Purpor[6],
                px.colors.sequential.RdPu[8]]

In [97]:
colorscales = []
for i in range(10):
    colorscales.append((((0,colorscales_orig[i]),(1,colorscales_orig[i]))))
    colorscales.append((((0,colorscales_orig[i]),(1,colorscales_orig[i]))))
colorscales1 = []
for i in range(10):
    colorscales1.append(colorscales_orig[i])
    colorscales1.append(colorscales_orig[i])
#die colorscales die wir unten im plot verwenden werden

In [98]:
def idk(county1):
    lene = []
    for county in df.county.unique():
        lene.append(len(df_map.loc[(df_map.county1 == county)|(df_map.county2 == county)].score.unique()))
    return(np.repeat((df.county.unique() == county1),np.array(lene)))

In [99]:
def idk2(values):
    alle = []
    for i in values:
        alle.append(colorscales1[i])
    return(alle)

2 Funktionen die jeweils arrays mit True und False werten zurückgeben (werden für den Plot gebraucht)

---Plot D3.1---

In [ ]:
fig = make_subplots(cols= 2, rows=2, specs= [[dict(type= "table"), dict(type= "choroplethmapbox", rowspan = 2)], [dict(type= "bar"), None]])

fig.add_trace(
  go.Table(
    columnwidth= [2, 4, 2, 2, 2],
    header=dict(
        values=list(df_table.columns)
        ),
    cells=dict(
        values=df_table.T.values,
        height= 28
        )
    ),
    col= 1,
    row= 1
)

# for county in df_map.county2.unique():

buttons1 = []
i = 0 
for county  in df.county.unique():   
    fig.add_trace(
            go.Bar(
                name=county,                
                y = df_map.loc[(df_map.county2 == county) | (df_map.county1 == county)].sort_values(by= "score", ascending= False).score.head(10),
                x = np.delete(df_map.loc[(df_map.county2 == county) | (df_map.county1 == county)].sort_values(by= "score", ascending= False)[["county1","county2"]].values.flatten(),df_map.loc[(df_map.county2 == county) | (df_map.county1 == county)].sort_values(by= "score", ascending= False)[["county1","county2"]].values.flatten() == county)[0:10],               
                #visible = False,
                showlegend= False,
                visible = False,
                marker_color = idk2(df_map.loc[(df_map.county2 == county) | (df_map.county1 == county)].sort_values(by= "score", ascending= False).score.head(10).values)
            ),
        col= 1,
        row= 2
        )


for county in df.county.unique():
    for i in df_map.loc[(df_map.county1 == county)|(df_map.county2 == county)].score.unique():
        
        fig.add_trace(
            go.Choroplethmapbox(
                name=str(i),
                geojson= geojsn,
                featureidkey= "properties.NAME",
                locations= np.delete(df_map.loc[((df_map.county2 == county)|(df_map.county1 == county))&(df_map.score == i)][["county1","county2"]].values.flatten(),df_map.loc[((df_map.county2 == county)|(df_map.county1 == county))&(df_map.score == i)][["county1","county2"]].values.flatten()==county),
                z= [i]*len(np.delete(df_map.loc[((df_map.county2 == county)|(df_map.county1 == county))&(df_map.score == i)][["county1","county2"]].values.flatten(),df_map.loc[((df_map.county2 == county)|(df_map.county1 == county))&(df_map.score == i)][["county1","county2"]].values.flatten()==county)),
                colorscale=colorscales[i],
                showlegend=True,
                showscale=False,
                marker_opacity=0.85,
                marker_line_width=0,
                visible = False
                
            ),
        col= 2,
        row= 1
        )
fig.update_layout(
    updatemenus= [
            dict(buttons= list([
                dict(
                    label= county,
                    method= "update",
                    args= [
                        dict(
                            
                            visible = (np.append(np.append([True],df.county.unique() == county),idk(county))),
                            headers= dict(
                                values=list(df_table.columns)
                                ),
                            cells= dict(
                                values= df_table.loc[df_table.county == county].T.values,
                                height= 28
                                ),
                            
                            )
                    ]
                )
                for county in df_table.county.unique().tolist()
            ]),
            direction= "down",
            xanchor= "left",
            x= -0.11,
            yanchor= "top",
            y= 1.1,
            showactive= True
            ),
        
    ]
)



fig.update_layout(mapbox_style="carto-positron", mapbox_zoom= 5.1, mapbox_center = {"lat": 37, "lon": -120}, height= 850)
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.update_layout(title= dict(text= "<b>Ähnlichkeit der Top 10 Produkten zwischen counties</b>", font_size= 20, xanchor= "center", yanchor= "top", y=0.975, x=0.475), 

)
fig.show()

In [ ]:
df_12= df.groupby("county").agg(order=("order_id","nunique")).reset_index()
liste1 = df_12.loc[df_12.order > df_12.order.median()].county.to_list()
liste2 = df_12.loc[df_12.order <= df_12.order.median()].county.to_list()

In [ ]:
stärkste_counties_score = 0
schwächste_counties_score = 0
len1 = 0
len2 = 0
for i in ableitung:
    if (i[1] in liste1 and i[2] in liste1):
        stärkste_counties_score = stärkste_counties_score + i[0]
        len1 = len1 + 1
    elif (i[1] in liste2 and i[2] in liste2):
        schwächste_counties_score = schwächste_counties_score + i[0]
        len2 = len2 + 1
stärkste_counties_score = stärkste_counties_score/len1
schwächste_counties_score = schwächste_counties_score/len2

In [ ]:
round(stärkste_counties_score,2)

13.39

Die Ähnlichkeit der 50% stärksten counties liegt nach unserer Skala bei 10.8

In [ ]:
round(schwächste_counties_score,2)

11.66

Die Ähnlichkeit der 50% schwächsten counties liegt nach unserer Skala bei 5.53

Dadurch zeigt sich, dass die counties mit mehr Besttelungen mehr Ähnlichkeiten unter den Top 10 Produkten besitzen als die counties mit weniger Bestellungen

### 3. Zusätzliche Fragestellungen:

Welche Produkte, Gänge, Kategorien in welchen counties unter-, über- und nur durchschnittlich vertreten sind

1.Gänge

In [ ]:
df_33 = df.groupby(["county","aisle"]).agg(anzahl=("aisle","count")).reset_index()
df_33["Gesamt"] = 0
counties = df_33.county.unique().tolist()
for i in counties:
    df_33.loc[df_33["county"] == i,"Gesamt"] = df_33[df_33.county == i].anzahl.sum()
df_33["Anteil"] = df_33.anzahl / df_33.Gesamt
df_33["Gesamtanteil"] = 0
aisle = df_33.aisle.unique().tolist()
for i in aisle:
    df_33.loc[df_33.aisle == i,"Gesamtanteil"] = df_33[df_33.aisle == i].anzahl.sum() / df_33.anzahl.sum()

In [ ]:
df_33[df_33.aisle == "yogurt"]

county   aisle  anzahl  Gesamt    Anteil  Gesamtanteil
132           Alameda  yogurt     933   16916  0.055155      0.044793
266            Alpine  yogurt    7092  133283  0.053210      0.044793
400            Amador  yogurt    4241  121112  0.035017      0.044793
534         Calaveras  yogurt   21949  502479  0.043681      0.044793
668            Colusa  yogurt    1706   34943  0.048822      0.044793
802      Contra Costa  yogurt    3566   96721  0.036869      0.044793
935         Del Norte  yogurt    1158   19310  0.059969      0.044793
1054        El Dorado  yogurt    1188   15423  0.077028      0.044793
1188           Fresno  yogurt   18052  357941  0.050433      0.044793
1322            Glenn  yogurt   17409  390414  0.044591      0.044793
1446         Humboldt  yogurt     203    6401  0.031714      0.044793
1580         Imperial  yogurt    6594  181121  0.036407      0.044793
1714             Inyo  yogurt    2295   54787  0.041889      0.044793
1848             Kern  yogurt   11685  292188  0.039991      0.044793
1981            Kings  yogurt    1574   38678  0.040695      0.044793
2115             Lake  yogurt    6094  144838  0.042075      0.044793
2244           Lassen  yogurt     842   23200  0.036293      0.044793
2378      Los Angeles  yogurt    7295  157398  0.046347      0.044793
2512           Madera  yogurt    7112  132423  0.053707      0.044793
2646            Marin  yogurt    3285   78183  0.042017      0.044793
2780         Mariposa  yogurt    9919  235808  0.042064      0.044793
2913        Mendocino  yogurt    2851   52310  0.054502      0.044793
3047           Merced  yogurt    6828  155346  0.043953      0.044793
3181            Modoc  yogurt    5903   95082  0.062083      0.044793
3309             Mono  yogurt    1597   29865  0.053474      0.044793
3443         Monterey  yogurt   10331  240793  0.042904      0.044793
3577             Napa  yogurt     673   17749  0.037918      0.044793
3711           Nevada  yogurt    3053   59370  0.051423      0.044793
3845           Orange  yogurt   18701  395915  0.047235      0.044793
4029           Plumas  yogurt    2072   59409  0.034877      0.044793
4163        Riverside  yogurt    2117   47673  0.044407      0.044793
4297       Sacramento  yogurt    4434   94953  0.046697      0.044793
4431       San Benito  yogurt    2846   83712  0.033998      0.044793
4605        San Diego  yogurt     614   24320  0.025247      0.044793
4739    San Francisco  yogurt    6780  144710  0.046852      0.044793
4868      San Joaquin  yogurt     185    8103  0.022831      0.044793
5002  San Luis Obispo  yogurt    1469   34670  0.042371      0.044793
5131        San Mateo  yogurt    3610   91149  0.039605      0.044793
5264    Santa Barbara  yogurt    7598  173526  0.043786      0.044793
5398      Santa Clara  yogurt    4260   95219  0.044739      0.044793
5532       Santa Cruz  yogurt    6863  158869  0.043199      0.044793
5666           Shasta  yogurt    1315   40145  0.032756      0.044793
5799           Sierra  yogurt    1567   29582  0.052971      0.044793
5933         Siskiyou  yogurt    2308   70133  0.032909      0.044793
6064           Solano  yogurt    1889   36500  0.051753      0.044793
6196           Sonoma  yogurt    1058   16568  0.063858      0.044793
6330       Stanislaus  yogurt    1134   27309  0.041525      0.044793
6464           Sutter  yogurt   12853  286497  0.044863      0.044793
6592           Tehama  yogurt     718    8787  0.081712      0.044793
6683          Trinity  yogurt      25    1419  0.017618      0.044793
6809           Tulare  yogurt     952   16380  0.058120      0.044793
6939         Tuolumne  yogurt    1173   32033  0.036618      0.044793
7073          Ventura  yogurt   12087  250125  0.048324      0.044793
7206             Yolo  yogurt    2401   70556  0.034030      0.044793
7340             Yuba  yogurt    8243  149919  0.054983      0.044793

In [ ]:
df_22 =pd.DataFrame(columns=df_33.columns)
aisle = df_33.aisle.unique().tolist()
for i in aisle:
    df_22 = pd.concat([df_22,df_33.loc[(df_33.aisle == i)&(df_33.Anteil >df_33[df_33.aisle == i].Anteil.quantile(0.75))]])

In [ ]:
df_22

county                         aisle anzahl  Gesamt    Anteil  \
1447    Imperial        air fresheners candles    259  181121   0.00143   
1581        Inyo        air fresheners candles     61   54787  0.001113   
1849       Kings        air fresheners candles     43   38678  0.001112   
2116      Lassen        air fresheners candles     32   23200  0.001379   
2513       Marin        air fresheners candles    108   78183  0.001381   
...          ...                           ...    ...     ...       ...   
5949      Solano  bulk grains rice dried goods     31   36500  0.000849   
6212  Stanislaus  bulk grains rice dried goods     42   27309  0.001538   
6480      Tehama  bulk grains rice dried goods      6    8787  0.000683   
6698      Tulare  bulk grains rice dried goods     43   16380  0.002625   
7089        Yolo  bulk grains rice dried goods    189   70556  0.002679   

     Gesamtanteil  
1447     0.000611  
1581     0.000611  
1849     0.000611  
2116     0.000611  
2513     0.000611  
...           ...  
5949     0.000558  
6212     0.000558  
6480     0.000558  
6698     0.000558  
7089     0.000558  

[1852 rows x 6 columns]

In [ ]:
df_99 =pd.DataFrame(columns=df_33.columns)
aisle = df_33.aisle.unique().tolist()
for i in aisle:
    df_99 = pd.concat([df_99,df_33.loc[(df_33.aisle == i)&(df_33.Anteil <df_33[df_33.aisle == i].Anteil.quantile(0.25))]])

In [ ]:
df_99

county                         aisle anzahl  Gesamt    Anteil  \
0       Alameda        air fresheners candles      6   16916  0.000355   
936   El Dorado        air fresheners candles      1   15423  0.000065   
1715       Kern        air fresheners candles     80  292188  0.000274   
2379     Madera        air fresheners candles     42  132423  0.000317   
3182       Mono        air fresheners candles      3   29865    0.0001   
...         ...                           ...    ...     ...       ...   
5548     Shasta  bulk grains rice dried goods      2   40145   0.00005   
5681     Sierra  bulk grains rice dried goods      1   29582  0.000034   
5815   Siskiyou  bulk grains rice dried goods     11   70133  0.000157   
6079     Sonoma  bulk grains rice dried goods      3   16568  0.000181   
7222       Yuba  bulk grains rice dried goods      8  149919  0.000053   

     Gesamtanteil  
0        0.000611  
936      0.000611  
1715     0.000611  
2379     0.000611  
3182     0.000611  
...           ...  
5548     0.000558  
5681     0.000558  
5815     0.000558  
6079     0.000558  
7222     0.000558  

[1852 rows x 6 columns]

In [ ]:
relevant = []
for i in df_22.values:
    df_0 = df_22.loc[(df_22.county == i[0])&(df_22.aisle == i[1])][["county","anzahl","Gesamt"]]   
    ch2, p, dof, expected = chi2_contingency(df_0.append(dict(county = "alle",anzahl=df_33[df_33.aisle == i[1]].anzahl.sum(),Gesamt = df_33[df_33.aisle == i[1]].Gesamt.sum() ),ignore_index= True).set_index("county"))
    if p < 0.05:
            relevant.append(i)

C:\Users\paulh\AppData\Local\Temp\ipykernel_23680\1053801759.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\paulh\AppData\Local\Temp\ipykernel_23680\1053801759.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\paulh\AppData\Local\Temp\ipykernel_23680\1053801759.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\paulh\AppData\Local\Temp\ipykernel_23680\1053801759.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\paulh\AppData\Local\Temp\ipykernel_23680\1053801759.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat 

In [ ]:
relevant1 = []
for i in df_99.values:
    df_0 = df_99.loc[(df_99.county == i[0])&(df_99.aisle == i[1])][["county","anzahl","Gesamt"]]   
    ch2, p, dof, expected = chi2_contingency(df_0.append(dict(county = "alle",anzahl=df_33[df_33.aisle == i[1]].anzahl.sum(),Gesamt = df_33[df_33.aisle == i[1]].Gesamt.sum() ),ignore_index= True).set_index("county"))
    if p < 0.05:
            relevant1.append(i)

C:\Users\paulh\AppData\Local\Temp\ipykernel_23680\3661270059.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\paulh\AppData\Local\Temp\ipykernel_23680\3661270059.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\paulh\AppData\Local\Temp\ipykernel_23680\3661270059.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\paulh\AppData\Local\Temp\ipykernel_23680\3661270059.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\paulh\AppData\Local\Temp\ipykernel_23680\3661270059.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat 

In [ ]:
df_tes1 = pd.DataFrame(relevant,columns=df_88.columns)

In [ ]:
df_tes1

county                         aisle  anzahl  Gesamt    Anteil  \
0          Imperial        air fresheners candles     259  181121  0.001430   
1              Inyo        air fresheners candles      61   54787  0.001113   
2             Kings        air fresheners candles      43   38678  0.001112   
3            Lassen        air fresheners candles      32   23200  0.001379   
4             Marin        air fresheners candles     108   78183  0.001381   
...             ...                           ...     ...     ...       ...   
1659  Santa Barbara  bulk grains rice dried goods     483  173526  0.002783   
1660         Solano  bulk grains rice dried goods      31   36500  0.000849   
1661     Stanislaus  bulk grains rice dried goods      42   27309  0.001538   
1662         Tulare  bulk grains rice dried goods      43   16380  0.002625   
1663           Yolo  bulk grains rice dried goods     189   70556  0.002679   

      Gesamtanteil  
0         0.000611  
1         0.000611  
2         0.000611  
3         0.000611  
4         0.000611  
...            ...  
1659      0.000558  
1660      0.000558  
1661      0.000558  
1662      0.000558  
1663      0.000558  

[1664 rows x 6 columns]

Dataframe mit allen relevanten Gängen die in entsprechenden counties mehr nachgefragt werden

In [ ]:
df_tes2 = pd.DataFrame(relevant1,columns=df_99.columns)

In [ ]:
df_tes2

county                         aisle  anzahl  Gesamt    Anteil  \
0      El Dorado        air fresheners candles       1   15423  0.000065   
1           Kern        air fresheners candles      80  292188  0.000274   
2         Madera        air fresheners candles      42  132423  0.000317   
3           Mono        air fresheners candles       3   29865  0.000100   
4         Nevada        air fresheners candles      10   59370  0.000168   
...          ...                           ...     ...     ...       ...   
1619  Santa Cruz  bulk grains rice dried goods      32  158869  0.000201   
1620      Shasta  bulk grains rice dried goods       2   40145  0.000050   
1621      Sierra  bulk grains rice dried goods       1   29582  0.000034   
1622    Siskiyou  bulk grains rice dried goods      11   70133  0.000157   
1623        Yuba  bulk grains rice dried goods       8  149919  0.000053   

      Gesamtanteil  
0         0.000611  
1         0.000611  
2         0.000611  
3         0.000611  
4         0.000611  
...            ...  
1619      0.000558  
1620      0.000558  
1621      0.000558  
1622      0.000558  
1623      0.000558  

[1624 rows x 6 columns]

Dataframe mit allen relevanten Gängen die in entsprechenden counties weniger nachgefragt werden

2.Kategorien

In [ ]:
df_dep = df.groupby(["county","department"]).agg(anzahl=("department","count")).reset_index()
df_dep["Gesamt"] = 0
counties = df_dep.county.unique().tolist()
for i in counties:
    df_dep.loc[df_dep["county"] == i,"Gesamt"] = df_dep[df_dep.county == i].anzahl.sum()
df_dep["Anteil"] = df_dep.anzahl / df_dep.Gesamt
df_dep["Gesamtanteil"] = 0
department = df_dep.department.unique().tolist()
for i in department:
    df_dep.loc[df_dep.department == i,"Gesamtanteil"] = df_dep[df_dep.department == i].anzahl.sum() / df_dep.anzahl.sum()

In [ ]:
df_dep

county     department  anzahl  Gesamt    Anteil  Gesamtanteil
0     Alameda        alcohol     170   16916  0.010050      0.004622
1     Alameda         babies      40   16916  0.002365      0.013227
2     Alameda         bakery     500   16916  0.029558      0.036467
3     Alameda      beverages    2294   16916  0.135611      0.083414
4     Alameda      breakfast     351   16916  0.020750      0.022141
...       ...            ...     ...     ...       ...           ...
1168     Yuba         pantry    3244  149919  0.021638      0.057995
1169     Yuba  personal care    3078  149919  0.020531      0.013968
1170     Yuba           pets     552  149919  0.003682      0.003027
1171     Yuba        produce   30046  149919  0.200415      0.289255
1172     Yuba         snacks   20799  149919  0.138735      0.089397

[1173 rows x 6 columns]

In [ ]:
df_dep1 =pd.DataFrame(columns=df_dep.columns)
department = df_dep.department.unique().tolist()
for i in department:
    df_dep1 = pd.concat([df_dep1,df_dep.loc[(df_dep.department == i)&(df_dep.Anteil >df_dep[df_dep.department == i].Anteil.quantile(0.75))]])

In [ ]:
df_dep1

county department anzahl  Gesamt    Anteil Gesamtanteil
126        Del Norte    alcohol    569   19310  0.029467     0.004622
209         Humboldt    alcohol    639    6401  0.099828     0.004622
230         Imperial    alcohol   2151  181121  0.011876     0.004622
314             Lake    alcohol   2178  144838  0.015037     0.004622
335           Lassen    alcohol    618   23200  0.026638     0.004622
...              ...        ...    ...     ...       ...          ...
620           Placer     snacks     40     258  0.155039     0.089397
716   San Bernardino     snacks     25     148  0.168919     0.089397
737        San Diego     snacks   2845   24320  0.116982     0.089397
925           Sierra     snacks   3652   29582  0.123453     0.089397
1172            Yuba     snacks  20799  149919  0.138735     0.089397

[293 rows x 6 columns]

In [ ]:
df_dep2 =pd.DataFrame(columns=df_dep.columns)
department = df_dep.department.unique().tolist()
for i in department:
    df_dep2 = pd.concat([df_dep2,df_dep.loc[(df_dep.department == i)&(df_dep.Anteil < df_dep[df_dep.department == i].Anteil.quantile(0.25))]])

In [ ]:
df_dep2

county department anzahl  Gesamt    Anteil Gesamtanteil
63        Calaveras    alcohol    552  502479  0.001099     0.004622
272            Kern    alcohol    461  292188  0.001578     0.004622
293           Kings    alcohol     46   38678  0.001189     0.004622
356     Los Angeles    alcohol    186  157398  0.001182     0.004622
461          Merced    alcohol     52  155346  0.000335     0.004622
...             ...        ...    ...     ...       ...          ...
841   Santa Barbara     snacks  13704  173526  0.078974     0.089397
988          Sonoma     snacks    502   16568  0.030299     0.089397
1009     Stanislaus     snacks   1385   27309  0.050716     0.089397
1068        Trinity     snacks     21    1419  0.014799     0.089397
1088         Tulare     snacks    702   16380  0.042857     0.089397

[293 rows x 6 columns]

In [ ]:
relevant3 = []
for i in df_dep1.values:
    df_0 = df_dep1.loc[(df_dep1.county == i[0])&(df_dep1.department == i[1])][["county","anzahl","Gesamt"]]   
    ch2, p, dof, expected = chi2_contingency(df_0.append(dict(county = "alle",anzahl=df_dep[df_dep.department == i[1]].anzahl.sum(),Gesamt = df_dep[df_dep.department == i[1]].Gesamt.sum() ),ignore_index= True).set_index("county"))
    if p < 0.05:
            relevant3.append(i)

C:\Users\paulh\AppData\Local\Temp\ipykernel_19280\3215021303.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\paulh\AppData\Local\Temp\ipykernel_19280\3215021303.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\paulh\AppData\Local\Temp\ipykernel_19280\3215021303.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\paulh\AppData\Local\Temp\ipykernel_19280\3215021303.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\paulh\AppData\Local\Temp\ipykernel_19280\3215021303.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat 

In [ ]:
relevant4 = []
for i in df_dep2.values:
    df_0 = df_dep2.loc[(df_dep2.county == i[0])&(df_dep2.department == i[1])][["county","anzahl","Gesamt"]]   
    ch2, p, dof, expected = chi2_contingency(df_0.append(dict(county = "alle",anzahl=df_dep[df_dep.department == i[1]].anzahl.sum(),Gesamt = df_dep[df_dep.department == i[1]].Gesamt.sum() ),ignore_index= True).set_index("county"))
    if p < 0.05:
            relevant4.append(i)

C:\Users\paulh\AppData\Local\Temp\ipykernel_19280\3291703908.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\paulh\AppData\Local\Temp\ipykernel_19280\3291703908.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\paulh\AppData\Local\Temp\ipykernel_19280\3291703908.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\paulh\AppData\Local\Temp\ipykernel_19280\3291703908.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\paulh\AppData\Local\Temp\ipykernel_19280\3291703908.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat 

In [ ]:
df_tes3 = pd.DataFrame(relevant3,columns=df_dep1.columns)

In [ ]:
df_tes3

county department  anzahl  Gesamt    Anteil  Gesamtanteil
0         Del Norte    alcohol     569   19310  0.029467      0.004622
1          Humboldt    alcohol     639    6401  0.099828      0.004622
2          Imperial    alcohol    2151  181121  0.011876      0.004622
3              Lake    alcohol    2178  144838  0.015037      0.004622
4            Lassen    alcohol     618   23200  0.026638      0.004622
..              ...        ...     ...     ...       ...           ...
274          Placer     snacks      40     258  0.155039      0.089397
275  San Bernardino     snacks      25     148  0.168919      0.089397
276       San Diego     snacks    2845   24320  0.116982      0.089397
277          Sierra     snacks    3652   29582  0.123453      0.089397
278            Yuba     snacks   20799  149919  0.138735      0.089397

[279 rows x 6 columns]

Dataframe mit allen relevanten Kategorien die in entsprechenden counties mehr nachgefragt werden

In [ ]:
df_tes4 = pd.DataFrame(relevant4,columns=df_dep2.columns)

In [ ]:
df_tes4

county department  anzahl  Gesamt    Anteil  Gesamtanteil
0        Calaveras    alcohol     552  502479  0.001099      0.004622
1             Kern    alcohol     461  292188  0.001578      0.004622
2            Kings    alcohol      46   38678  0.001189      0.004622
3      Los Angeles    alcohol     186  157398  0.001182      0.004622
4           Merced    alcohol      52  155346  0.000335      0.004622
..             ...        ...     ...     ...       ...           ...
278  Santa Barbara     snacks   13704  173526  0.078974      0.089397
279         Sonoma     snacks     502   16568  0.030299      0.089397
280     Stanislaus     snacks    1385   27309  0.050716      0.089397
281        Trinity     snacks      21    1419  0.014799      0.089397
282         Tulare     snacks     702   16380  0.042857      0.089397

[283 rows x 6 columns]

Dataframe mit allen relevanten Kategorien die in entsprechenden counties weniger nachgefragt werden

In [ ]:
colorscales_2 = dict(
                durchschnittlich=((0,"grey"),(1,"grey")),
                unterdurchschnittlich=((0,"red"),(1,"red")),
                überdruchschnittlich=((0,"green"),(1,"green"))
                )

In [ ]:
df_category = df.groupby(["county","department"]).agg(demand=("department","nunique")).reset_index()
for county in df_category.county.unique():
    oversought = df_tes3[df_tes3.county == county].department.to_list()
    undersought = df_tes4[df_tes4.county == county].department.to_list()
    df_category.loc[(df_category.county == county)&(df_category.department.isin(oversought)),"demand"] = "überdruchschnittlich"
    df_category.loc[(df_category.county == county)&(df_category.department.isin(undersought)),"demand"] = "unterdurchschnittlich"
    df_category.loc[(df_category.county == county)&(~(df_category.department.isin(undersought))&~(df_category.department.isin(oversought))),"demand"] = "durchschnittlich"

In [ ]:
allen = []
for department in df_category.department.unique():
    allen.append(len(df_category.loc[df_category.department == department].demand.unique()))

In [ ]:
np.array([2,1]).reshape(1,2)

array([[2, 1]])

In [ ]:
df_dep["Anteil"]= df_dep.Anteil.round(4)

In [ ]:
df_dep["Gesamtanteil"]= df_dep.Gesamtanteil.round(4)

---Plot D0.4---

In [ ]:
fig = make_subplots(cols= 2, rows=1, specs= [[dict(type= "table"), dict(type= "choroplethmapbox")]])

fig.add_trace(
  go.Table(
    columnwidth= [2, 4, 2, 2, 2],
    header=dict(
        values=list(df_dep.columns)
        ),
    cells=dict(
        values=df_dep.T.values,
        height= 28
        )
    ),
    col= 1,
    row= 1
)

for department in df_category.department.unique():
    for i,b in enumerate(df_category.loc[df_category.department == department].demand.unique()):
        
        fig.add_trace(
            go.Choroplethmapbox(
                name=str(b),
                geojson= geojsn,
                featureidkey= "properties.NAME",
                locations= df_category.loc[(df_category.department == department)&(df_category.demand == b)].county,
                z= [i]*len(df_category.loc[(df_category.department == department)&(df_category.demand == b)]),
                colorscale=colorscales_2[b],
                showlegend=True,
                showscale=False,
                marker_opacity=0.85,
                marker_line_width=0,
                visible = False
                
            ),
            col= 2,
            row= 1
        
        )
fig.update_layout(
    updatemenus= [
            dict(buttons= list([
                dict(
                    label= department,
                    method= "update",
                    args= [
                        dict(
                            
                            visible = np.append([True],np.repeat(df_category.department.unique() == department,allen)),
                            headers= dict(
                                values=list(df_dep.columns)
                                ),
                            cells= dict(
                                values= df_dep.loc[df_dep.department == department].T.values,
                                height= 28
                                ),
                   
                            )
                    ]
                )
                for department in df_category.department.unique().tolist()
            ]),
            direction= "down",
            xanchor= "left",
            x= -0.11,
            yanchor= "top",
            y= 1.1,
            showactive= True
            ),
        
    ]
)



fig.update_layout(mapbox_style="carto-positron", mapbox_zoom= 5.1, mapbox_center = {"lat": 37, "lon": -120}, height= 850)
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.update_layout(title= dict(text= "<b>Nachfrage nach Kategorien pro County</b>", font_size= 20, xanchor= "center", yanchor= "top", y=0.975, x=0.475)),
fig.show()

3.Produkte

Da es in unserem Datensatz sehr viele verschieden Produkte gibt müssen wir die erstmalige Suche eingrenzen.

Wir haben uns dafür entschlossen nur Produkte zu betrachten die in wenigstens 25 counties vertreten sind

In [ ]:
df_pro = df.groupby("product_name").agg(counti = ("county","nunique")).reset_index()

In [ ]:
df_pro[df_pro.counti > 20].product_name.to_list()

['#2 Coffee Filters',
 '0% Fat Free Organic Milk',
 '0% Fat Organic Greek Vanilla Yogurt',
 '0% Fat Superfruits Greek Yogurt',
 '0% Greek Strained Yogurt',
 '0% Greek Yogurt Black Cherry on the Bottom',
 '0% Greek, Blueberry on the Bottom Yogurt',
 '1 % Lowfat Milk',
 '1 Apple + 1 Mango Fruit Bar',
 '1 Apple + 1 Pear Fruit Bar',
 '1 Liter',
 '1 Ply Paper Towels',
 '1 Step Kashmir Spinach Indian Cuisine',
 '1% Low Fat Chocolate Milk',
 '1% Low Fat Milk',
 '1% Lowfat Milk',
 '1% Milkfat Low Fat Buttermilk',
 '1% Milkfat Low Fat Vitamin A & D Milk',
 '1% Milkfat Lowfat Cottage Cheese',
 '1/3 Less Fat Cream Cheese',
 '100 Calorie  Per Bag Popcorn',
 '100 Calorie Pretzels Packs',
 '100% Apple Juice',
 '100% Apple Juice, Original',
 '100% Baby Kale',
 '100% Cacao Unsweetened Chocolate Baking Bar',
 '100% Carrot Juice',
 '100% Colombian Medium Dark Roast Ground Coffee',
 '100% Cranberry Juice',
 '100% Florida Orange Juice',
 '100% Grass-Fed Organic Plain Creamline Yogurt',
 '100% Grated Parme

In [ ]:
df_pro1 = df.groupby(["county","product_name"]).agg(anzahl=("product_name","count")).reset_index()
df_pro1 = df_pro1[df_pro1.product_name.isin(df_pro[df_pro.counti > 40].product_name.to_list())]

In [ ]:
df_pro1

county                                       product_name  anzahl  \
9       Alameda                        100% Grated Parmesan Cheese       1   
11      Alameda                    100% Lactose Free Fat Free Milk       8   
13      Alameda                                   100% Lemon Juice       2   
28      Alameda                                  100% Pure Pumpkin       1   
29      Alameda                             100% Raw Coconut Water      71   
...         ...                                                ...     ...   
579109     Yuba                         Yellow Straightneck Squash      18   
579121     Yuba       YoKids Blueberry & Strawberry/Vanilla Yogurt      39   
579124     Yuba  YoKids Squeezers Organic Low-Fat Yogurt, Straw...      41   
579144     Yuba                  Yogurt, Strained Low-Fat, Coconut      87   
579154     Yuba                        Yukon Gold Potatoes 5lb Bag      18   

        Gesamt    Anteil  
9         7567  0.000132  
11        7567  0.001057  
13        7567  0.000264  
28        7567  0.000132  
29        7567  0.009383  
...        ...       ...  
579109   53737  0.000335  
579121   53737  0.000726  
579124   53737  0.000763  
579144   53737  0.001619  
579154   53737  0.000335  

[30522 rows x 5 columns]

In [ ]:
df_pro1 = df.groupby(["county","product_name"]).agg(anzahl=("product_name","count")).reset_index()
df_pro1 = df_pro1[df_pro1.product_name.isin(df_pro[df_pro.counti > 50].product_name.to_list())]
df_pro1["Gesamt"] = 0
counties = df_pro1.county.unique().tolist()
for i in counties:
    df_pro1.loc[df_pro1["county"] == i,"Gesamt"] = df_pro1[df_pro1.county == i].anzahl.sum()
df_pro1["Anteil"] = df_pro1.anzahl / df_pro1.Gesamt
# df_pro1["Gesamtanteil"] = 0
# product_name = df_pro1.product_name.unique().tolist()
# for i in product_name:
#     df_pro1.loc[df_pro1.product_name == i,"Gesamtanteil"] = df_pro1[df_pro1.product_name == i].anzahl.sum() / df_pro1.anzahl.sum()

In [ ]:
df_pro2 =pd.DataFrame(columns=df_pro1.columns)
product_name = df_pro1.product_name.unique().tolist()
for i in product_name:
    df_pro2 = pd.concat([df_pro2,df_pro1.loc[(df_pro1.product_name == i)&(df_pro1.Anteil >df_pro1[df_pro1.product_name == i].Anteil.quantile(0.75))]])

In [ ]:
df_pro2

county                 product_name anzahl Gesamt    Anteil
71198    Del Norte  100% Grated Parmesan Cheese      5   6725  0.000743
124148    Imperial  100% Grated Parmesan Cheese     55  68401  0.000804
177051        Lake  100% Grated Parmesan Cheese     53  62150  0.000853
192555      Lassen  100% Grated Parmesan Cheese     16   6999  0.002286
226694       Marin  100% Grated Parmesan Cheese     29  27547  0.001053
...            ...                          ...    ...    ...       ...
368617   Riverside   Yellow Straightneck Squash     12  18094  0.000663
379068  Sacramento   Yellow Straightneck Squash     42  48035  0.000874
494324      Solano   Yellow Straightneck Squash     10  15501  0.000645
498153      Sonoma   Yellow Straightneck Squash      7   7643  0.000916
530954      Tulare   Yellow Straightneck Squash      5   7892  0.000634

[7708 rows x 5 columns]

In [ ]:
df_pro3 =pd.DataFrame(columns=df_pro1.columns)
product_name = df_pro1.product_name.unique().tolist()
for i in product_name:
    df_pro3 = pd.concat([df_pro3,df_pro1.loc[(df_pro1.product_name == i)&(df_pro1.Anteil < df_pro1[df_pro1.product_name == i].Anteil.quantile(0.25))]])

In [ ]:
df_pro3

county                 product_name anzahl Gesamt    Anteil
9           Alameda  100% Grated Parmesan Cheese      1   7567  0.000132
17402        Amador  100% Grated Parmesan Cheese     13  54225   0.00024
53788        Colusa  100% Grated Parmesan Cheese      1  16411  0.000061
266314       Merced  100% Grated Parmesan Cheese     15  65783  0.000228
292005         Mono  100% Grated Parmesan Cheese      1  14020  0.000071
...             ...                          ...    ...    ...       ...
328941       Nevada   Yellow Straightneck Squash      5  25468  0.000196
449000  Santa Clara   Yellow Straightneck Squash      6  37827  0.000159
477419       Sierra   Yellow Straightneck Squash      1   9309  0.000107
504212   Stanislaus   Yellow Straightneck Squash      1  12012  0.000083
536787     Tuolumne   Yellow Straightneck Squash      3  13329  0.000225

[7708 rows x 5 columns]

weil es so viele unterschiedliche Produkte gibt und eine Suche auf allen Produkte sehr lange dauern würde grenzen wir entsprechend unsere Suche ein

In [ ]:
relevant5 = []
for i in df_pro2.values:
    df_0 = df_pro2.loc[(df_pro2.county == i[0])&(df_pro2.product_name == i[1])][["county","anzahl","Gesamt"]]   
    ch2, p, dof, expected = chi2_contingency(df_0.append(dict(county = "alle",anzahl=df_pro1[df_pro1.product_name == i[1]].anzahl.sum(),Gesamt = df_pro1[df_pro1.product_name == i[1]].Gesamt.sum() ),ignore_index= True).set_index("county"))
    if p < 0.05:
            relevant5.append(i)

C:\Users\paulh\AppData\Local\Temp\ipykernel_23680\1483219749.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\paulh\AppData\Local\Temp\ipykernel_23680\1483219749.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\paulh\AppData\Local\Temp\ipykernel_23680\1483219749.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\paulh\AppData\Local\Temp\ipykernel_23680\1483219749.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\paulh\AppData\Local\Temp\ipykernel_23680\1483219749.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat 

In [ ]:
relevant6 = []
for i in df_pro3.values:
    df_0 = df_pro3.loc[(df_pro3.county == i[0])&(df_pro3.product_name == i[1])][["county","anzahl","Gesamt"]]   
    ch2, p, dof, expected = chi2_contingency(df_0.append(dict(county = "alle",anzahl=df_pro1[df_pro1.product_name == i[1]].anzahl.sum(),Gesamt = df_pro1[df_pro1.product_name == i[1]].Gesamt.sum() ),ignore_index= True).set_index("county"))
    if p < 0.05:
            relevant6.append(i)

C:\Users\paulh\AppData\Local\Temp\ipykernel_23680\4277334003.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\paulh\AppData\Local\Temp\ipykernel_23680\4277334003.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\paulh\AppData\Local\Temp\ipykernel_23680\4277334003.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\paulh\AppData\Local\Temp\ipykernel_23680\4277334003.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat instead.

C:\Users\paulh\AppData\Local\Temp\ipykernel_23680\4277334003.py:4: FutureWarning:

The frame.append method is deprecated and will be removed from pandas in a future version. Use pandas.concat 

In [ ]:
df_tes5 = pd.DataFrame(relevant5,columns=df_pro2.columns)

In [ ]:
df_tes5

county                 product_name  anzahl  Gesamt    Anteil
0        Imperial  100% Grated Parmesan Cheese      55   68401  0.000804
1            Lake  100% Grated Parmesan Cheese      53   62150  0.000853
2          Lassen  100% Grated Parmesan Cheese      16    6999  0.002286
3           Marin  100% Grated Parmesan Cheese      29   27547  0.001053
4     San Joaquin  100% Grated Parmesan Cheese       5    3426  0.001459
...           ...                          ...     ...     ...       ...
5709        Kings   Yellow Straightneck Squash      15   14618  0.001026
5710         Lake   Yellow Straightneck Squash      60   62150  0.000965
5711     Mariposa   Yellow Straightneck Squash      63   95270  0.000661
5712       Plumas   Yellow Straightneck Squash      19   25601  0.000742
5713   Sacramento   Yellow Straightneck Squash      42   48035  0.000874

[5714 rows x 5 columns]

Dataframe mit allen relevanten Produkten die in entsprechenden counties mehr nachgefragt werden

In [ ]:
df_tes6 = pd.DataFrame(relevant6,columns=df_pro3.columns)

In [ ]:
df_tes6

county                 product_name  anzahl  Gesamt    Anteil
0          Colusa  100% Grated Parmesan Cheese       1   16411  0.000061
1          Merced  100% Grated Parmesan Cheese      15   65783  0.000228
2      Sacramento  100% Grated Parmesan Cheese       7   48035  0.000146
3      San Benito  100% Grated Parmesan Cheese       5   34603  0.000144
4       San Mateo  100% Grated Parmesan Cheese       1   43985  0.000023
...           ...                          ...     ...     ...       ...
5107        Glenn   Yellow Straightneck Squash      38  151216  0.000251
5108       Madera   Yellow Straightneck Squash      11   53351  0.000206
5109       Merced   Yellow Straightneck Squash      15   65783  0.000228
5110        Modoc   Yellow Straightneck Squash       3   33804  0.000089
5111  Santa Clara   Yellow Straightneck Squash       6   37827  0.000159

[5112 rows x 5 columns]

Dataframe mit allen relevanten Produkten die in entsprechenden counties weniger nachgefragt werden